# Bayesian Diagnosis Simulation
This notebook simulates medical diagnoses using Bayesian probability updates with varying parameters.

In [2]:
import os, sys

nb_dir = os.path.split(os.getcwd())[0]
if nb_dir not in sys.path:
    sys.path.append(nb_dir)

import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from notebooks.utilities import create_bayes_animation
from IPython.display import HTML

$P(A|B) = \frac{P(B|A) \cdot P(A)}{P(B)}$

Where:
- $P(A|B)$ = Posterior Probability
- $P(B|A)$ = Likelihood
- $P(A)$ = Prior Probability
- $P(B)$ = Evidence


In [3]:
def compute_bayes_rule(
    p_cancer, p_test_positive_given_no_cancer, p_test_positive_given_cancer
):
    # We need to add up the two cases that make up the positive test
    # p(test positive) = p(test positive | cancer) * p_cancer + p(test positive | no cancer) * p_no_cancer
    p_test_positive = (p_test_positive_given_cancer * p_cancer) + (
        p_test_positive_given_no_cancer * (1 - p_cancer)
    )

    # Simulating negative tests as well
    # p(test negative) = p(test negative | cancer) + p(test negative | no cancer)
    # p(test negative | cancer) = 1 - p(test positive | cancer)
    # p(test negative | no cancer) = 1 - p(test positive | no cancer)
    p_test_negative = ((1 - p_test_positive_given_cancer) * p_cancer) + (
        (1 - p_test_positive_given_no_cancer) * (1 - p_cancer)
    )

    # Ultimately, as we know more information from the diagnoses, we want to know how our p(cancer) belief changes
    # This p(cancer), based on the Bayes rule can either come from p(cancer | test positive) or p(cancer | test negative)
    # Posterior Updates
    # p(cancer | test positive) = p(test positive | cancer) * p(cancer) / p(test positive)
    p_cancer_given_test_positive = (
        p_test_positive_given_cancer * p_cancer / p_test_positive
    )
    # p(cancer | test negative) = p(test negative | cancer) * p(cancer) / p(test negative)
    #                           = (1 - p(test positive | cancer)) * p(cancer) / p(test negative)
    p_cancer_given_test_negative = (
        (1 - p_test_positive_given_cancer) * p_cancer / p_test_negative
    )
    return {
        "p_cancer_given_test_positive": round(p_cancer_given_test_positive, 2),
        "p_cancer_given_test_negative": round(p_cancer_given_test_negative, 2),
        "p_test_negative": round(p_test_negative, 2),
        "p_test_positive": round(p_test_positive, 2),
    }

In [4]:
def simulate_scenario(
    N: int, p_cancer: float, accuracy_range: tuple, false_positive_range: tuple
):
    """
    Simluation a single diagnosis scenario.
    N = number of simulations
    p_cancer = prior probability of cancer
    accuracy_range = range of test accuracy
    false_positive_range = range of false positive rate
    """
    accuracies = [round(np.random.uniform(*accuracy_range), 2) for _ in range(N)]
    false_positives = [
        round(np.random.uniform(*false_positive_range), 2) for _ in range(N)
    ]

    p_cancer_values = [p_cancer]
    parameters = []

    for i in range(N):
        probs = compute_bayes_rule(
            p_cancer=p_cancer,
            p_test_positive_given_cancer=accuracies[i],
            p_test_positive_given_no_cancer=false_positives[i],
        )

        # Determine diagnosis result (20% chance of positive)
        if np.random.random() < 0.2:
            p_cancer = probs["p_cancer_given_test_positive"]
            diagnosis = "Positive"
        else:
            p_cancer = probs["p_cancer_given_test_negative"]
            diagnosis = "Negative"

        p_cancer_values.append(p_cancer)
        parameters.append((accuracies[i], false_positives[i], p_cancer, diagnosis))

    return p_cancer_values, parameters

In [9]:
# Run simulations for all scenarios
N = 25
parameter_sets = [
    # Probability of cancer, Accuracy range, False positive range, Description
    (0.005, (0.8, 0.9), (0.01, 0.03), "normal case"),
    (0.5, (0.5, 0.5), (0.01, 0.5), "high initial self-doubt + high variance"),
    (0.005, (0.3, 0.5), (0.3, 0.5), "high false-positive and low accuracy rate"),
]

results = [
    simulate_scenario(N, p_cancer, acc_range, fp_range)
    for p_cancer, acc_range, fp_range, _ in parameter_sets
]
all_p_cancer_values, all_parameters = zip(*results)

animation = create_bayes_animation(
    N=N,
    parameter_sets=parameter_sets,
    all_p_cancer_values=all_p_cancer_values,
    all_parameters=all_parameters,
)

# Clear any existing plots
plt.close("all")

# Display the animation in the notebook
plt.show()
HTML(animation.to_jshtml())